In [1]:
from bs4 import BeautifulSoup
from selenium.webdriver import ActionChains
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from selenium import webdriver
from datetime import date,datetime,timedelta
import time
import sys
import os
import pandas as pd
import xlwt

In [2]:
#kobis 데이터 수집 시작
print("----------------------------------------------------------------")
print("<KOBIS 일별 박스오피스 크롤링을 시작합니다.>")
print()

# KOBIS (일별 박스오피스) 페이지 접속하기
path = "C:\\web_driver\\chromedriver.exe"
driver = webdriver.Chrome(path)
driver.get("https://www.kobis.or.kr/kobis/business/stat/boxs/findDailyBoxOfficeList.do")
time.sleep(3)

----------------------------------------------------------------
<KOBIS 일별 박스오피스 크롤링을 시작합니다.>



C:\Users\admin\AppData\Local\Temp\ipykernel_11640\2265360381.py:8: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(path)


In [ ]:
# 날짜 입력 후 조회하기
start_date = date(2022, 10, 14)
end_date = date(2022, 10, 20)

rank_list=[]
movie_info_cont=[]

#전체 차트 수집하기(rank_list=[])
while start_date <= end_date :
    try :
        # 시작날짜 입력
        date_from=driver.find_element(By.XPATH,'//*[@id="sSearchFrom"]')
        for i in range(10):
            date_from.send_keys(Keys.BACKSPACE) 
        date_from.send_keys(start_date.strftime("%Y-%m-%d")) 

        # 종료날짜 입력
        date_to=driver.find_element(By.XPATH,'//*[@id="sSearchTo"]')
        for j in range(10):
            date_to.send_keys(Keys.BACKSPACE)
        date_to.send_keys(start_date.strftime("%Y-%m-%d"))

        # 조회 버튼 클릭
        search_btn=driver.find_element(By.XPATH,'//*[@id="searchForm"]/div/div[5]/button')
        search_btn.click()
        time.sleep(1)

        start_date+=timedelta(days=1)

        #더보기 클릭하여 전체 자료보기
        while True :
            try :
                driver.find_element(By.LINK_TEXT,"더보기").click()
            except :
                break
        
        # 페이지 읽어오기       
        full_html=driver.page_source
        soup=BeautifulSoup(full_html, 'html.parser')

        # 검색날짜 
        search_date=soup.find('div','board_tit').get_text().replace("\n","")

        # 검색건수
        search_total=soup.find('em','fwb').get_text()
        print(search_total)

        # 컬럼 리스트 생성
        content_column=soup.find('thead').find_all('th',{'scope':'col'})
        column_list=[]
        column_list.append('일자')
        for column in content_column :
            column_list.append(column.text.replace("\t","").replace("\n","").replace("오름차순내림차순",""))
        print(column_list)

        # 항목 리스트 생성
        rank_table=soup.find('tbody').find_all('tr')

        #리스트에 항목 담기
        for movie in rank_table :
            chart=[]
            chart.append(search_date)

            #영화 순위
            movie_rank=movie.find('td').text.replace("\t","").replace("\n","")
            chart.append(movie_rank)

            #영화제목
            movie_title=movie.find('span','ellip per90').get_text()
            chart.append(movie_title)

            #개봉일
            movie_chart=movie.select('td:nth-child(3)')
            for date in movie_chart :
                chart.append(date.text.replace("\n","").replace("\t","").replace(" ",""))

            #'매출액', '매출액점유율', '매출액증감(전일대비)', '누적매출액', '관객수' 등
            movie_chart=movie.find_all('td','tar')
            for record in movie_chart :
                chart.append(record.text.replace("\t","").replace("\n",""))

            rank_list.append(chart)
            
        print(rank_list)
        
# 영화별 세부정보 수집하기 (movie_info_cont=[])
        movie_name_list=soup.find_all('span','ellip per90')
        for k in movie_name_list :
            try :
                name=k.get_text()

                # 영화 정보 팝업 띄우기
                movie_info=[]
                
                if all(name not in movie_info for movie_info in movie_info_cont):
                    movie_btn=driver.find_element(By.LINK_TEXT,str(name))
                    movie_btn.click()
                    time.sleep(1)

                    #영화 정보 가져오기
                    movie_html=driver.page_source
                    soup=BeautifulSoup(movie_html, 'html.parser')

                    #영화제목
                    movie_name=soup.find('div','hd_layer').find('strong').get_text()
                    movie_info.append(movie_name)

                    #영화세부정보contents
                    movie_contents=soup.find('dl',class_='ovf cont').find_all('dd')
                    for cont in movie_contents :
                        movie_info.append(cont.text.replace("\n","").replace("\t","").replace(" ","").strip())

                    #감독, 배우 정보 수집
                    try : 
                        movie_staff_dict={'감독' : [],'배우' : []}
                        director=soup.find('div','staffMore').find('dd').text.strip()
                        movie_staff_dict['감독'].append(director)
                        actor_list=soup.find('div','staffMore').find('td').find_all('a')
                        for actor in actor_list :
                            movie_staff_dict['배우'].append(actor.text.strip())
                        movie_info.append(movie_staff_dict)

                    except : 
                        movie_staff_dict={'감독' : [],'배우' : []}
                        movie_info.append(movie_staff_dict)
                    
                    #영화제목,세부정보,감독,배우 movie_info_cont 리스트에 담기
                    movie_info_cont.append(movie_info)
                    print(movie_info_cont)

                    # 팝업 창 닫기
                    time.sleep(1)
                    driver.find_element(By.LINK_TEXT,"뒤로").click()
                    
            except : 
                print("오류 항목을 제외합니다.")
                continue

    except :
        print("데이터를 수집하지 못하였습니다.")
        break

137
['일자', '순위', '영화명', '개봉일', '매출액', '매출액점유율', '매출액증감(전일대비)', '누적매출액', '관객수', '관객수증감(전일대비)', '누적관객수', '스크린수', '상영횟수']
[['2022년 10월 14일(금)', '1', '공조2: 인터내셔날', '2022-09-07', '231,688,862', '17.3%', '85,778,198(58.8%)', '68,525,382,022', '29,010', '11,475(65.4%)', '6,689,128', '833', '2,627'], ['2022년 10월 14일(금)', '2', '인생은 아름다워', '2022-09-28', '246,116,254', '18.4%', '66,301,514(36.9%)', '6,973,662,805', '27,636', '7,376(36.4%)', '733,217', '882', '2,835'], ['2022년 10월 14일(금)', '3', '오펀: 천사의 탄생', '2022-10-12', '178,686,338', '13.3%', '58,585,587(48.8%)', '467,578,547', '17,370', '5,196(42.7%)', '47,071', '662', '1,915'], ['2022년 10월 14일(금)', '4', '정직한 후보2', '2022-09-28', '132,108,386', '9.9%', '38,043,390(40.4%)', '7,525,707,165', '15,765', '4,920(45.4%)', '792,527', '691', '1,734'], ['2022년 10월 14일(금)', '5', '극장판 짱구는 못말려: 수수께끼! 꽃피는 천하떡잎학교', '2022-09-28', '95,695,763', '7.1%', '38,352,684(66.9%)', '4,832,760,314', '9,409', '3,609(62.2%)', '483,075', '448', '752'], ['2022년 10월 14일(금)', 

[['공조2: 인터내셔날', '20215601', '해당정보없음', '공조2인터내셔날(ConfidentialAssignment2International)', '장편|일반영화|액션,코미디|128분31초|15세이상관람가|한국', '2022-09-07', '2021년', '개봉', '2021-02-16~2021-06-15', '75회', '2D:디지털(20215601D),디지털가치봄(20215601L)', {'감독': ['이석훈'], '배우': ['현빈', '유해진', '임윤아', '다니엘 헤니', '진선규']}]]
[['공조2: 인터내셔날', '20215601', '해당정보없음', '공조2인터내셔날(ConfidentialAssignment2International)', '장편|일반영화|액션,코미디|128분31초|15세이상관람가|한국', '2022-09-07', '2021년', '개봉', '2021-02-16~2021-06-15', '75회', '2D:디지털(20215601D),디지털가치봄(20215601L)', {'감독': ['이석훈'], '배우': ['현빈', '유해진', '임윤아', '다니엘 헤니', '진선규']}], ['인생은 아름다워', '20198317', '해당정보없음', '해당정보없음', '장편|일반영화|뮤지컬|122분25초|12세이상관람가|한국', '2022-09-28', '2020년', '개봉', '2019-10-14~2020-02-06', '해당정보없음', '2D:디지털(20198317D),디지털가치봄(20198317L)4D:4D(20198317F)', {'감독': ['최국희'], '배우': ['류승룡(강진봉)', '염정아(오세연)', '박세완(여고생 세연)', '옹성우(정우)']}]]
[['공조2: 인터내셔날', '20215601', '해당정보없음', '공조2인터내셔날(ConfidentialAssignment2International)', '장편|일반영화|액션,코미디|128분31초|15세이상관람가|한국', '2022-09-07', '2021년'

[['공조2: 인터내셔날', '20215601', '해당정보없음', '공조2인터내셔날(ConfidentialAssignment2International)', '장편|일반영화|액션,코미디|128분31초|15세이상관람가|한국', '2022-09-07', '2021년', '개봉', '2021-02-16~2021-06-15', '75회', '2D:디지털(20215601D),디지털가치봄(20215601L)', {'감독': ['이석훈'], '배우': ['현빈', '유해진', '임윤아', '다니엘 헤니', '진선규']}], ['인생은 아름다워', '20198317', '해당정보없음', '해당정보없음', '장편|일반영화|뮤지컬|122분25초|12세이상관람가|한국', '2022-09-28', '2020년', '개봉', '2019-10-14~2020-02-06', '해당정보없음', '2D:디지털(20198317D),디지털가치봄(20198317L)4D:4D(20198317F)', {'감독': ['최국희'], '배우': ['류승룡(강진봉)', '염정아(오세연)', '박세완(여고생 세연)', '옹성우(정우)']}], ['오펀: 천사의 탄생', '20227304', '해당정보없음', '오펀천사의탄생,오펀퍼스트킬,오펀:천사의비밀프리퀄,오펀프리퀄(OrphanFirstKill,Esther)', '장편|일반영화|공포(호러),스릴러|98분21초|15세이상관람가|미국', '2022-10-12', '2022년', '개봉', '해당정보없음', '해당정보없음', '2D:디지털(20227304D)', {'감독': ['윌리엄 브렌트 벨'], '배우': ['이사벨 퍼만', '줄리아 스타일즈', '로지프 서덜랜드']}], ['정직한 후보2', '20219628', '해당정보없음', '해당정보없음', '장편|일반영화|코미디|106분43초|12세이상관람가|한국', '좌충우돌코미디', '2022-09-28', '2022년', '개봉', '2021-07-31~2021-10-31', '해당정보없음', '2D:디지털(

[['공조2: 인터내셔날', '20215601', '해당정보없음', '공조2인터내셔날(ConfidentialAssignment2International)', '장편|일반영화|액션,코미디|128분31초|15세이상관람가|한국', '2022-09-07', '2021년', '개봉', '2021-02-16~2021-06-15', '75회', '2D:디지털(20215601D),디지털가치봄(20215601L)', {'감독': ['이석훈'], '배우': ['현빈', '유해진', '임윤아', '다니엘 헤니', '진선규']}], ['인생은 아름다워', '20198317', '해당정보없음', '해당정보없음', '장편|일반영화|뮤지컬|122분25초|12세이상관람가|한국', '2022-09-28', '2020년', '개봉', '2019-10-14~2020-02-06', '해당정보없음', '2D:디지털(20198317D),디지털가치봄(20198317L)4D:4D(20198317F)', {'감독': ['최국희'], '배우': ['류승룡(강진봉)', '염정아(오세연)', '박세완(여고생 세연)', '옹성우(정우)']}], ['오펀: 천사의 탄생', '20227304', '해당정보없음', '오펀천사의탄생,오펀퍼스트킬,오펀:천사의비밀프리퀄,오펀프리퀄(OrphanFirstKill,Esther)', '장편|일반영화|공포(호러),스릴러|98분21초|15세이상관람가|미국', '2022-10-12', '2022년', '개봉', '해당정보없음', '해당정보없음', '2D:디지털(20227304D)', {'감독': ['윌리엄 브렌트 벨'], '배우': ['이사벨 퍼만', '줄리아 스타일즈', '로지프 서덜랜드']}], ['정직한 후보2', '20219628', '해당정보없음', '해당정보없음', '장편|일반영화|코미디|106분43초|12세이상관람가|한국', '좌충우돌코미디', '2022-09-28', '2022년', '개봉', '2021-07-31~2021-10-31', '해당정보없음', '2D:디지털(

[['공조2: 인터내셔날', '20215601', '해당정보없음', '공조2인터내셔날(ConfidentialAssignment2International)', '장편|일반영화|액션,코미디|128분31초|15세이상관람가|한국', '2022-09-07', '2021년', '개봉', '2021-02-16~2021-06-15', '75회', '2D:디지털(20215601D),디지털가치봄(20215601L)', {'감독': ['이석훈'], '배우': ['현빈', '유해진', '임윤아', '다니엘 헤니', '진선규']}], ['인생은 아름다워', '20198317', '해당정보없음', '해당정보없음', '장편|일반영화|뮤지컬|122분25초|12세이상관람가|한국', '2022-09-28', '2020년', '개봉', '2019-10-14~2020-02-06', '해당정보없음', '2D:디지털(20198317D),디지털가치봄(20198317L)4D:4D(20198317F)', {'감독': ['최국희'], '배우': ['류승룡(강진봉)', '염정아(오세연)', '박세완(여고생 세연)', '옹성우(정우)']}], ['오펀: 천사의 탄생', '20227304', '해당정보없음', '오펀천사의탄생,오펀퍼스트킬,오펀:천사의비밀프리퀄,오펀프리퀄(OrphanFirstKill,Esther)', '장편|일반영화|공포(호러),스릴러|98분21초|15세이상관람가|미국', '2022-10-12', '2022년', '개봉', '해당정보없음', '해당정보없음', '2D:디지털(20227304D)', {'감독': ['윌리엄 브렌트 벨'], '배우': ['이사벨 퍼만', '줄리아 스타일즈', '로지프 서덜랜드']}], ['정직한 후보2', '20219628', '해당정보없음', '해당정보없음', '장편|일반영화|코미디|106분43초|12세이상관람가|한국', '좌충우돌코미디', '2022-09-28', '2022년', '개봉', '2021-07-31~2021-10-31', '해당정보없음', '2D:디지털(

...

[['공조2: 인터내셔날', '20215601', '해당정보없음', '공조2인터내셔날(ConfidentialAssignment2International)', '장편|일반영화|액션,코미디|128분31초|15세이상관람가|한국', '2022-09-07', '2021년', '개봉', '2021-02-16~2021-06-15', '75회', '2D:디지털(20215601D),디지털가치봄(20215601L)', {'감독': ['이석훈'], '배우': ['현빈', '유해진', '임윤아', '다니엘 헤니', '진선규']}], ['인생은 아름다워', '20198317', '해당정보없음', '해당정보없음', '장편|일반영화|뮤지컬|122분25초|12세이상관람가|한국', '2022-09-28', '2020년', '개봉', '2019-10-14~2020-02-06', '해당정보없음', '2D:디지털(20198317D),디지털가치봄(20198317L)4D:4D(20198317F)', {'감독': ['최국희'], '배우': ['류승룡(강진봉)', '염정아(오세연)', '박세완(여고생 세연)', '옹성우(정우)']}], ['오펀: 천사의 탄생', '20227304', '해당정보없음', '오펀천사의탄생,오펀퍼스트킬,오펀:천사의비밀프리퀄,오펀프리퀄(OrphanFirstKill,Esther)', '장편|일반영화|공포(호러),스릴러|98분21초|15세이상관람가|미국', '2022-10-12', '2022년', '개봉', '해당정보없음', '해당정보없음', '2D:디지털(20227304D)', {'감독': ['윌리엄 브렌트 벨'], '배우': ['이사벨 퍼만', '줄리아 스타일즈', '로지프 서덜랜드']}], ['정직한 후보2', '20219628', '해당정보없음', '해당정보없음', '장편|일반영화|코미디|106분43초|12세이상관람가|한국', '좌충우돌코미디', '2022-09-28', '2022년', '개봉', '2021-07-31~2021-10-31', '해당정보없음', '2D:디지털(

[['공조2: 인터내셔날', '20215601', '해당정보없음', '공조2인터내셔날(ConfidentialAssignment2International)', '장편|일반영화|액션,코미디|128분31초|15세이상관람가|한국', '2022-09-07', '2021년', '개봉', '2021-02-16~2021-06-15', '75회', '2D:디지털(20215601D),디지털가치봄(20215601L)', {'감독': ['이석훈'], '배우': ['현빈', '유해진', '임윤아', '다니엘 헤니', '진선규']}], ['인생은 아름다워', '20198317', '해당정보없음', '해당정보없음', '장편|일반영화|뮤지컬|122분25초|12세이상관람가|한국', '2022-09-28', '2020년', '개봉', '2019-10-14~2020-02-06', '해당정보없음', '2D:디지털(20198317D),디지털가치봄(20198317L)4D:4D(20198317F)', {'감독': ['최국희'], '배우': ['류승룡(강진봉)', '염정아(오세연)', '박세완(여고생 세연)', '옹성우(정우)']}], ['오펀: 천사의 탄생', '20227304', '해당정보없음', '오펀천사의탄생,오펀퍼스트킬,오펀:천사의비밀프리퀄,오펀프리퀄(OrphanFirstKill,Esther)', '장편|일반영화|공포(호러),스릴러|98분21초|15세이상관람가|미국', '2022-10-12', '2022년', '개봉', '해당정보없음', '해당정보없음', '2D:디지털(20227304D)', {'감독': ['윌리엄 브렌트 벨'], '배우': ['이사벨 퍼만', '줄리아 스타일즈', '로지프 서덜랜드']}], ['정직한 후보2', '20219628', '해당정보없음', '해당정보없음', '장편|일반영화|코미디|106분43초|12세이상관람가|한국', '좌충우돌코미디', '2022-09-28', '2022년', '개봉', '2021-07-31~2021-10-31', '해당정보없음', '2D:디지털(

[['공조2: 인터내셔날', '20215601', '해당정보없음', '공조2인터내셔날(ConfidentialAssignment2International)', '장편|일반영화|액션,코미디|128분31초|15세이상관람가|한국', '2022-09-07', '2021년', '개봉', '2021-02-16~2021-06-15', '75회', '2D:디지털(20215601D),디지털가치봄(20215601L)', {'감독': ['이석훈'], '배우': ['현빈', '유해진', '임윤아', '다니엘 헤니', '진선규']}], ['인생은 아름다워', '20198317', '해당정보없음', '해당정보없음', '장편|일반영화|뮤지컬|122분25초|12세이상관람가|한국', '2022-09-28', '2020년', '개봉', '2019-10-14~2020-02-06', '해당정보없음', '2D:디지털(20198317D),디지털가치봄(20198317L)4D:4D(20198317F)', {'감독': ['최국희'], '배우': ['류승룡(강진봉)', '염정아(오세연)', '박세완(여고생 세연)', '옹성우(정우)']}], ['오펀: 천사의 탄생', '20227304', '해당정보없음', '오펀천사의탄생,오펀퍼스트킬,오펀:천사의비밀프리퀄,오펀프리퀄(OrphanFirstKill,Esther)', '장편|일반영화|공포(호러),스릴러|98분21초|15세이상관람가|미국', '2022-10-12', '2022년', '개봉', '해당정보없음', '해당정보없음', '2D:디지털(20227304D)', {'감독': ['윌리엄 브렌트 벨'], '배우': ['이사벨 퍼만', '줄리아 스타일즈', '로지프 서덜랜드']}], ['정직한 후보2', '20219628', '해당정보없음', '해당정보없음', '장편|일반영화|코미디|106분43초|12세이상관람가|한국', '좌충우돌코미디', '2022-09-28', '2022년', '개봉', '2021-07-31~2021-10-31', '해당정보없음', '2D:디지털(

[['공조2: 인터내셔날', '20215601', '해당정보없음', '공조2인터내셔날(ConfidentialAssignment2International)', '장편|일반영화|액션,코미디|128분31초|15세이상관람가|한국', '2022-09-07', '2021년', '개봉', '2021-02-16~2021-06-15', '75회', '2D:디지털(20215601D),디지털가치봄(20215601L)', {'감독': ['이석훈'], '배우': ['현빈', '유해진', '임윤아', '다니엘 헤니', '진선규']}], ['인생은 아름다워', '20198317', '해당정보없음', '해당정보없음', '장편|일반영화|뮤지컬|122분25초|12세이상관람가|한국', '2022-09-28', '2020년', '개봉', '2019-10-14~2020-02-06', '해당정보없음', '2D:디지털(20198317D),디지털가치봄(20198317L)4D:4D(20198317F)', {'감독': ['최국희'], '배우': ['류승룡(강진봉)', '염정아(오세연)', '박세완(여고생 세연)', '옹성우(정우)']}], ['오펀: 천사의 탄생', '20227304', '해당정보없음', '오펀천사의탄생,오펀퍼스트킬,오펀:천사의비밀프리퀄,오펀프리퀄(OrphanFirstKill,Esther)', '장편|일반영화|공포(호러),스릴러|98분21초|15세이상관람가|미국', '2022-10-12', '2022년', '개봉', '해당정보없음', '해당정보없음', '2D:디지털(20227304D)', {'감독': ['윌리엄 브렌트 벨'], '배우': ['이사벨 퍼만', '줄리아 스타일즈', '로지프 서덜랜드']}], ['정직한 후보2', '20219628', '해당정보없음', '해당정보없음', '장편|일반영화|코미디|106분43초|12세이상관람가|한국', '좌충우돌코미디', '2022-09-28', '2022년', '개봉', '2021-07-31~2021-10-31', '해당정보없음', '2D:디지털(

[['공조2: 인터내셔날', '20215601', '해당정보없음', '공조2인터내셔날(ConfidentialAssignment2International)', '장편|일반영화|액션,코미디|128분31초|15세이상관람가|한국', '2022-09-07', '2021년', '개봉', '2021-02-16~2021-06-15', '75회', '2D:디지털(20215601D),디지털가치봄(20215601L)', {'감독': ['이석훈'], '배우': ['현빈', '유해진', '임윤아', '다니엘 헤니', '진선규']}], ['인생은 아름다워', '20198317', '해당정보없음', '해당정보없음', '장편|일반영화|뮤지컬|122분25초|12세이상관람가|한국', '2022-09-28', '2020년', '개봉', '2019-10-14~2020-02-06', '해당정보없음', '2D:디지털(20198317D),디지털가치봄(20198317L)4D:4D(20198317F)', {'감독': ['최국희'], '배우': ['류승룡(강진봉)', '염정아(오세연)', '박세완(여고생 세연)', '옹성우(정우)']}], ['오펀: 천사의 탄생', '20227304', '해당정보없음', '오펀천사의탄생,오펀퍼스트킬,오펀:천사의비밀프리퀄,오펀프리퀄(OrphanFirstKill,Esther)', '장편|일반영화|공포(호러),스릴러|98분21초|15세이상관람가|미국', '2022-10-12', '2022년', '개봉', '해당정보없음', '해당정보없음', '2D:디지털(20227304D)', {'감독': ['윌리엄 브렌트 벨'], '배우': ['이사벨 퍼만', '줄리아 스타일즈', '로지프 서덜랜드']}], ['정직한 후보2', '20219628', '해당정보없음', '해당정보없음', '장편|일반영화|코미디|106분43초|12세이상관람가|한국', '좌충우돌코미디', '2022-09-28', '2022년', '개봉', '2021-07-31~2021-10-31', '해당정보없음', '2D:디지털(

In [ ]:
kobis_rank=pd.DataFrame()
kobis_rank["영화순위"]=rank_list
kobis_rank.to_csv("kobis_rank.csv", encoding='utf-8-sig', index=False)

kobis_movie_info=pd.DataFrame()
kobis_movie_info["영화상세정보"]=movie_info_cont
kobis_movie_info.to_csv("kobis_movie_info.csv", encoding='utf-8-sig', index=False)